In [ ]:
import sys
import django
import os
file_dir = "/Users/mirbilal/Desktop/MobCommission/commissionV2/"
if file_dir not in sys.path:
    sys.path.insert(0, file_dir)

os.environ["DJANGO_SETTINGS_MODULE"] = "commissionerv2.settings"
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true" 
django.setup()
from apps.environment.models.stock import StockBuffer
from apps.environment_simulator.sevice_layer.stock_simulator import StockSimulator
import numpy as np
import json
from datetime import datetime
from dateutil.relativedelta import relativedelta
import pytz
import pandas as pd
import cufflinks as cf
from django.db.models import Q
from os import path, environ
from apps.environment.service_layer.data_transformer import DataTransformer
import plotly.graph_objs as go
from apps.environment.models.stock import Stock


In [6]:


nwb_starting_time_step = datetime(year=2020, month=4, day=1)
# now_time = pytz.utc.localize(datetime(year=2023, month=1, day=1))
now_time = pytz.utc.localize(datetime.now())
# nwb_starting_time_step = datetime.now() - relativedelta(days=360)
# nwb_starting_time_step = nwb_starting_time_step.strftime('%Y-%m-%d %H:%M:%S')
# nwb_starting_time_step = datetime.strptime(nwb_starting_time_step, "%Y-%m-%d %H:%M:%S")

nwb_db_params = {
    'database': environ.get("POSTGRES_DB"),
    'user': environ.get("POSTGRES_USER"),
    'password': environ.get("POSTGRES_PASSWORD"),
    'host': environ.get("DB_HOST"),
    'port': environ.get("DB_PORT"),
}
nwb_env_config = {
    "db_params": nwb_db_params, 
    "max_episode_steps": 100, 
    "the_current_time_step": nwb_starting_time_step,
    "print_output": False,
    "is_test": False,
    "test_steps": 200,
    "n_step_stocks": 5,
    "n_step_cmmdties": 5,
    "preparing": False,
    "no_of_stocks": 100,
    "no_of_cmmdts": 14,
    "is_live": True,
    # "temp_data_date": "2024-01-02"
} 
nwb_dformer = DataTransformer(env_config=nwb_env_config)
nwb_dfs = nwb_dformer.create_input_dataframes()
stck_buffs = nwb_dfs[2]
# pd.set_option('display.max_rows', None)
# temp_df = stck_buffs[stck_buffs["index"] == 29][['captured_at', 'price_snapshot', 'x_day_ma']]
# temp_df = temp_df[temp_df['captured_at'] <= '2023-01-01'].tail(20)
# display(temp_df)
stck_buffs = stck_buffs[stck_buffs['captured_at'] <= '2021-01-01']
stck_buffs['captured_at'] = pd.to_datetime(stck_buffs['captured_at'])  # Ensure 'captured_at' is in datetime format
stck_buffs.sort_values(by='captured_at', inplace=True)  # Sort DataFrame by 'captured_at' in ascending order



cf.go_offline()
cf.set_config_file(world_readable=True, theme="white")

stck_buffs['captured_at'] = pd.to_datetime(stck_buffs['captured_at'])
stck_buffs.set_index('captured_at', inplace=True)

grouped_df = stck_buffs.groupby('index')[['price_snapshot', 'x_day_ma', 'volume']]

layout = go.Layout(
    xaxis=dict(title='Captured At'),
    yaxis=dict(title='Price Snapshot', side='left'),
    yaxis2=dict(title='Volume', side='right', overlaying='y')
)

stck_objs: list[Stock] = Stock.objects.all()
stck_names = {}

for stk in stck_objs:
    stck_names[stk.index] = stk

for stock_index, group_data in grouped_df:
    price_snapshot_group = group_data['price_snapshot']
    volume_group = group_data['volume']
    ma_group = group_data['x_day_ma']

    # Plotting price_snapshot on the left y-axis
    trace_price = go.Scatter(
        x=price_snapshot_group.index,
        y=price_snapshot_group,
        mode='lines',
        name='Price Snapshot'
    )

    # Plotting volume on the right y-axis with filled bars using dashes
    # trace_volume = go.Bar(
    #     x=volume_group.index,
    #     y=volume_group,
    #     name='Volume',
    #     yaxis='y2',
    #     opacity=0.9,  # Adjust opacity for the bars
    #     marker=dict(color='black'),  # Set the color of the bars
    #     # visible = True,
    #     width=5
    # )
    trace_volume = go.Scatter(
        x=volume_group.index,
        y=volume_group,
        mode='lines',
        name='Volume',
        opacity=0.5,
        yaxis='y2',
        # line=dict(dash='dash')  # Set the dash pattern for the line
    )

    # Plotting 14-day moving average as a line on the left y-axis
    trace_ma = go.Scatter(
        x=ma_group.index,
        y=ma_group,
        mode='lines',
        name='indicator',
        line=dict(dash='dash')  # Set the dash pattern for the line
    )

    fig = go.Figure(data=[trace_price, trace_volume, trace_ma], layout=layout)
    # fig = go.Figure(data=[trace_volume], layout=layout)


    # Update the figure title with the stock index
    fig.update_layout(title=f'Price and Volume Over Time - Stock = {stock_index} {stck_names[stock_index].symbol}, {stck_names[stock_index].name}')

    # Show the figure
    fig.show()

/Users/mirbilal/Desktop/MobCommission/commissionV2/apps/environment/service_layer/data_transformer.py:392: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

/Users/mirbilal/Desktop/MobCommission/commissionV2/apps/environment/service_layer/data_transformer.py:393: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

/Users/mirbilal/Desktop/MobCommission/commissionV2/apps/environment/service_layer/data_transformer.py:422: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

/Users/mirbilal/Desktop/MobCommission/commissionV2/apps/environment/service_layer/data_transformer.py:423: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

